In [1]:
import json
from pathlib import Path

In [2]:
file_path = "/content/sample_data/hin_mixed_2019_30K-sentences.txt"

# Open and read the entire file
with open(file_path, "r", encoding="utf-8") as f:
    text = f.read()

# Optional: print first few characters to verify
print(text[:500])

1	00 डोंगरगढ़ के लिए ट्रेन और सड़क मार्ग दोनों ओर से रास्ता है।
2	02:02 PM: मुंबई पुलिस का कहना है कि जेल में अबू सलेम पर दो राउंड फायरिंग की गई, जिससे उसकी उंगली में चोट लग गई.
3	02:40 PMचुनावों में जीत के लिए नवाज शरीफ को प्रधानमंत्री मनमोहन सिंह और अफगानिस्तान के प्रेजिडेंट हामिद करजई ने बधाई दी।
4	03:22 PMआरुषि-हेमराज मर्डर केस में तलवार दंपती दोषी करार।
5	05.05 AM: इलाहाबाद में संगम तट पर भारी तादाद में जुटे श्रद्धालु.
6	08 : सबसे बड़ी जीत रनों के लिहाज से दक्षिण अफ्रीका ने हासिल की है।
7	0


In [52]:
pattern = re.compile(r'\p{Devanagari}+|\p{Latin}+|[^\p{L}\p{N}\s]+|\s+')

tokens = re.findall(pattern, text)
# Remove spaces and newlines
tokens = [t for t in tokens if not t.isspace()]

print("Initial tokens:", tokens)
print("Token count:", len(tokens))

Initial tokens: ['डोंगरगढ़', 'के', 'लिए', 'ट्रेन', 'और', 'सड़क', 'मार्ग', 'दोनों', 'ओर', 'से', 'रास्ता', 'है', '।', ':', 'PM', ':', 'मुंबई', 'पुलिस', 'का', 'कहना', 'है', 'कि', 'जेल', 'में', 'अबू', 'सलेम', 'पर', 'दो', 'राउंड', 'फायरिंग', 'की', 'गई', ',', 'जिससे', 'उसकी', 'उंगली', 'में', 'चोट', 'लग', 'गई', '.', ':', 'PM', 'चुनावों', 'में', 'जीत', 'के', 'लिए', 'नवाज', 'शरीफ', 'को', 'प्रधानमंत्री', 'मनमोहन', 'सिंह', 'और', 'अफगानिस्तान', 'के', 'प्रेजिडेंट', 'हामिद', 'करजई', 'ने', 'बधाई', 'दी', '।', ':', 'PM', 'आरुषि', '-', 'हेमराज', 'मर्डर', 'केस', 'में', 'तलवार', 'दंपती', 'दोषी', 'करार', '।', '.', 'AM', ':', 'इलाहाबाद', 'में', 'संगम', 'तट', 'पर', 'भारी', 'तादाद', 'में', 'जुटे', 'श्रद्धालु', '.', ':', 'सबसे', 'बड़ी', 'जीत', 'रनों', 'के', 'लिहाज', 'से', 'दक्षिण', 'अफ्रीका', 'ने', 'हासिल', 'की', 'है', '।', 'गोल्डी', 'पहले', 'किसी', 'और', 'विषय', 'पर', 'फिल्म', 'लिख', 'रहे', 'थे', '।', '१०१', '-', '१०२द्ध', 'जिस', 'प्रकार', 'तुलनात्मक', 'ढंग', 'से', 'कबीर', ',', 'तुलसीदास', 'और', 'नन्ददास', '-

In [3]:
tokens = text.encode("utf-8") # raw bytes
tokens = list(map(int, tokens)) # convert to a list of integers in range 0..255 for convenience
print(len(tokens))

7053637


In [4]:
def get_stats(ids):
    counts = {}
    for pair in zip(ids, ids[1:]):
        counts[pair] = counts.get(pair, 0) + 1
    return counts

def merge(ids, pair, idx):
    newids = []
    i = 0
    while i < len(ids):
        if i < len(ids) - 1 and ids[i] == pair[0] and ids[i+1] == pair[1]:
            newids.append(idx)
            i += 2
        else:
            newids.append(ids[i])
            i += 1
    return newids


# ==============================
# Step 4: Train BPE merges
# ==============================
vocab_size = 6000  # final vocab size
num_merges = vocab_size - 256

ids = list(tokens)
merges = {}  # (int, int) -> int

for i in range(num_merges):
    stats = get_stats(ids)
    if not stats:
        break
    pair = max(stats, key=stats.get)
    idx = 256 + i
    ids = merge(ids, pair, idx)
    merges[pair] = idx

print("Training complete.")
print("Original length:", len(tokens))
print("Compressed length:", len(ids))
print(f"Compression ratio: {len(tokens) / len(ids):.2f}X")

Training complete.
Original length: 7053637
Compressed length: 869484
Compression ratio: 8.11X


In [5]:
# ==============================
# Step 5: Encode function
# ==============================
def encode(text, merges):
    ids = list(text.encode("utf-8"))
    merges_r = {pair: idx for pair, idx in merges.items()}

    while True:
        stats = {pair: i for i, pair in enumerate(zip(ids, ids[1:])) if pair in merges_r}
        if not stats:
            break
        pair = min(stats, key=stats.get)
        new_id = merges_r[pair]
        new_ids = []
        i = 0
        while i < len(ids):
            if i < len(ids) - 1 and (ids[i], ids[i+1]) == pair:
                new_ids.append(new_id)
                i += 2
            else:
                new_ids.append(ids[i])
                i += 1
        ids = new_ids
    return ids

In [6]:
# ==============================
# Step 6: Decode function
# ==============================
def decode(ids, merges):
    merges_inv = {v: k for k, v in merges.items()}

    def expand(id_):
        if id_ < 256:
            return [id_]
        a, b = merges_inv[id_]
        return expand(a) + expand(b)

    bytes_out = []
    for id_ in ids:
        bytes_out.extend(expand(id_))
    return bytes(bytes_out).decode("utf-8", errors="replace")

In [7]:
# ==============================
# Step 8: Save tokenizer files
# ==============================
Path("tokenizer_output").mkdir(exist_ok=True)

# Save merges
with open("tokenizer_output/merges.json", "w", encoding="utf-8") as f:
    json.dump({f"{a},{b}": idx for (a, b), idx in merges.items()}, f, ensure_ascii=False, indent=2)

# Save vocab
vocab = {str(i): i for i in range(vocab_size)}
with open("tokenizer_output/vocab.json", "w", encoding="utf-8") as f:
    json.dump(vocab, f, ensure_ascii=False, indent=2)

# Save metadata
metadata = {
    "vocab_size": vocab_size,
    "num_merges": len(merges),
    "base_tokens": 256,
    "type": "custom Hindi BPE tokenizer"
}
with open("tokenizer_output/metadata.json", "w", encoding="utf-8") as f:
    json.dump(metadata, f, ensure_ascii=False, indent=2)

print("\nTokenizer files saved in `tokenizer_output/` folder:")
!ls tokenizer_output


Tokenizer files saved in `tokenizer_output/` folder:
merges.json  metadata.json  vocab.json


In [8]:
from google.colab import files
files.download("tokenizer_output/vocab.json")
files.download("tokenizer_output/merges.json")
files.download("tokenizer_output/metadata.json")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>